# Priming neural networks with the correct initializer.

In this quick experiment, we will be testing the effect of different weight/bias initializations on a very simple variational autoencoder (VAE). We will be using the MNIST dataset to prototype. The VAE will essentially have 3 layes:
- an input layer of shape (784) that would represent a flattened MNIST image (28,28).
- a single hidden layer where the input will be "encoded" down from 784 features to 32.
- an output layer that "decodes" the hidden latent representation back into a MNIST image.

In [53]:
import numpy as np
import tensorflow as tf
import plotly
from tensorflow.examples.tutorials.mnist import input_data
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly.graph_objs as go
init_notebook_mode(connected=True)
from plotly import tools
print ("tensorflow {}".format(tf.__version__))
print ("plotly {}".format(plotly.__version__))

tensorflow 1.4.1
plotly 2.2.3


## import data

In [54]:
mnist = input_data.read_data_sets('MNIST_data', validation_size=0)

Extracting MNIST_data/train-images-idx3-ubyte.gz
Extracting MNIST_data/train-labels-idx1-ubyte.gz
Extracting MNIST_data/t10k-images-idx3-ubyte.gz
Extracting MNIST_data/t10k-labels-idx1-ubyte.gz


## set various initializations

Here we pick 12 different tensorflow initializations to test.

In [85]:
initializers = [
# we start with the no brainer zeros and ones and constants
{"type":tf.zeros_initializer(), "name":"zeros"},
{"type":tf.ones_initializer(), "name":"ones"},
{"type":tf.constant_initializer(value=2), "name":"constant"},
    
# random distributions
{"type":tf.random_normal_initializer(mean=0.0,stddev=1.0), "name":"random_normal"},
{"type":tf.random_uniform_initializer(minval=0,maxval=1.0), "name":"random_uniform"},
    
# truncated distributions
{"type":tf.truncated_normal_initializer(mean=0.0,stddev=1.0), "name":"truncated_normal"},
    
# glorot or Xavier initalizations
{"type":tf.glorot_normal_initializer(), "name":"glorot_normal"},
{"type":tf.glorot_uniform_initializer(), "name":"glorot_uniform"},

# variance 
{"type":tf.variance_scaling_initializer(scale=1.0,distribution='normal'), "name":"variance_normal"},
{"type":tf.variance_scaling_initializer(scale=1.0,distribution='uniform'), "name":"variance_uniform"},
    
# others
{"type":tf.orthogonal_initializer(gain=1.0), "name":"orthogonal"},
{"type":tf.initializers.identity(gain=1.0), "name":"identity"}  
]

# add a loss list and value list to each entry in the list
for entry in initializers:
    entry["loss"] = [] 
    entry["value"] = [] 

## visualize initialization distributions

We will run generate square 2d matricies of shape 100*100 from each initalizer and plot their distribution, just to get an idea about how tensorflow samples them.

In [86]:
# set initializer value
for initializer in initializers:
    tf.reset_default_graph()
    with tf.Graph().as_default():
        # set seed
        tf.set_random_seed(42)
        # set dummy variable
        var = tf.Variable(initial_value=tf.get_variable(shape=[100,100],
                                                        name = initializer['name'],
                                                        initializer=initializer['type']))
        sess = tf.Session()
        init = tf.global_variables_initializer()
        sess.run(init)
        initializer['value'] = sess.run(var)

In [92]:
# plot distributions
# make figure
fig = tools.make_subplots(rows=4, cols=3, subplot_titles=[x['name'] for x in initializers])
for idx,initializer in enumerate(initializers):
    # make trace
    trace = go.Histogram(x=np.reshape(initializer['value'],100*100),histnorm='',opacity=0.6)
    fig.append_trace(trace, (idx//3) + 1, (idx%3) + 1 )
fig['layout'].update(height=1200, width=900, showlegend=False, title='Tensorflow initializer distribution - 10k samples')
iplot(fig) 

This is the format of your plot grid:
[ (1,1) x1,y1 ]    [ (1,2) x2,y2 ]    [ (1,3) x3,y3 ]  
[ (2,1) x4,y4 ]    [ (2,2) x5,y5 ]    [ (2,3) x6,y6 ]  
[ (3,1) x7,y7 ]    [ (3,2) x8,y8 ]    [ (3,3) x9,y9 ]  
[ (4,1) x10,y10 ]  [ (4,2) x11,y11 ]  [ (4,3) x12,y12 ]



## build model

In [49]:
epochs = 1
batch_size = 200

for initializer in initializers:
    tf.reset_default_graph()
    with tf.Graph().as_default():
        # set seed
        tf.set_random_seed(42)
        hidden_size = 32 
        # set weight and bias
        weight = {
            "i_h" : tf.Variable(initial_value=tf.get_variable(shape=[784,hidden_size],
                                                name="weight_i_h",
                                                initializer=initializer['type'])), 
            "h_o" : tf.Variable(initial_value=tf.get_variable(shape=[hidden_size,784],
                                                name="weight_h_o",
                                                initializer=initializer['type'])) 
        }  
        bias = {
            "i_h" : tf.Variable(initial_value= tf.zeros([hidden_size]) ),
            "h_o" :  tf.Variable(initial_value= tf.zeros([784]) ),
        }
        # placeholders
        _inputs = tf.placeholder(dtype=tf.float32,shape=[None,784],name="input_placeholder")
        _targets = tf.placeholder(dtype=tf.float32 ,shape=[None,784],name="target_placeholder")
        # encode
        encode = tf.nn.relu( tf.nn.bias_add ( tf.matmul(_inputs,weight["i_h"]) , bias["i_h"] ) ) 
        # logits
        logits =  tf.nn.bias_add( tf.matmul(encode,weight["h_o"]), bias["h_o"]) 
        # sigmoid 
        decode = tf.nn.sigmoid(logits)
        # cross-entropy 
        loss = tf.nn.sigmoid_cross_entropy_with_logits(logits=logits,labels=_targets)
        # mean
        cost = tf.reduce_mean(loss)
        # optimizer
        opt = tf.train.AdamOptimizer(learning_rate=0.001).minimize(cost)
        # session
        sess = tf.Session()
        init = tf.global_variables_initializer()
        sess.run(init)
        # run
        for epoch in range(epochs):
            for i in range(mnist.train.num_examples//batch_size):
                batch = mnist.train.next_batch(batch_size,shuffle=False)
                feed = {_inputs:batch[0],_targets:batch[0]}
                batch_cost, _ = sess.run([ cost, opt], feed_dict=feed)
                # add to list
                initializer['loss'].append(batch_cost)
                print("Epoch: {}/{} - ".format(epoch+1, epochs),"Training loss: {:.4f}".format(batch_cost))

Epoch: 1/1 -  Training loss: 0.6933
Epoch: 1/1 -  Training loss: 0.6930
Epoch: 1/1 -  Training loss: 0.6922
Epoch: 1/1 -  Training loss: 0.6919
Epoch: 1/1 -  Training loss: 0.6918
Epoch: 1/1 -  Training loss: 0.6914
Epoch: 1/1 -  Training loss: 0.6909
Epoch: 1/1 -  Training loss: 0.6904
Epoch: 1/1 -  Training loss: 0.6903
Epoch: 1/1 -  Training loss: 0.6900
Epoch: 1/1 -  Training loss: 0.6894
Epoch: 1/1 -  Training loss: 0.6890
Epoch: 1/1 -  Training loss: 0.6889
Epoch: 1/1 -  Training loss: 0.6886
Epoch: 1/1 -  Training loss: 0.6879
Epoch: 1/1 -  Training loss: 0.6875
Epoch: 1/1 -  Training loss: 0.6874
Epoch: 1/1 -  Training loss: 0.6870
Epoch: 1/1 -  Training loss: 0.6866
Epoch: 1/1 -  Training loss: 0.6860
Epoch: 1/1 -  Training loss: 0.6860
Epoch: 1/1 -  Training loss: 0.6857
Epoch: 1/1 -  Training loss: 0.6851
Epoch: 1/1 -  Training loss: 0.6850
Epoch: 1/1 -  Training loss: 0.6846
Epoch: 1/1 -  Training loss: 0.6844
Epoch: 1/1 -  Training loss: 0.6839
Epoch: 1/1 -  Training loss:

Epoch: 1/1 -  Training loss: 0.6159
Epoch: 1/1 -  Training loss: 0.6149
Epoch: 1/1 -  Training loss: 0.6149
Epoch: 1/1 -  Training loss: 0.6113
Epoch: 1/1 -  Training loss: 0.6128
Epoch: 1/1 -  Training loss: 0.6121
Epoch: 1/1 -  Training loss: 0.6126
Epoch: 1/1 -  Training loss: 0.6114
Epoch: 1/1 -  Training loss: 0.6100
Epoch: 1/1 -  Training loss: 0.6096
Epoch: 1/1 -  Training loss: 0.6100
Epoch: 1/1 -  Training loss: 0.6098
Epoch: 1/1 -  Training loss: 0.6097
Epoch: 1/1 -  Training loss: 0.6096
Epoch: 1/1 -  Training loss: 0.6095
Epoch: 1/1 -  Training loss: 0.6115
Epoch: 1/1 -  Training loss: 0.6099
Epoch: 1/1 -  Training loss: 0.6082
Epoch: 1/1 -  Training loss: 0.6072
Epoch: 1/1 -  Training loss: 0.6059
Epoch: 1/1 -  Training loss: 0.6048
Epoch: 1/1 -  Training loss: 0.6087
Epoch: 1/1 -  Training loss: 0.6053
Epoch: 1/1 -  Training loss: 0.6069
Epoch: 1/1 -  Training loss: 0.6071
Epoch: 1/1 -  Training loss: 0.6062
Epoch: 1/1 -  Training loss: 0.6047
Epoch: 1/1 -  Training loss:

Epoch: 1/1 -  Training loss: 1980.3989
Epoch: 1/1 -  Training loss: 1978.7600
Epoch: 1/1 -  Training loss: 1945.5237
Epoch: 1/1 -  Training loss: 1862.0894
Epoch: 1/1 -  Training loss: 1991.4351
Epoch: 1/1 -  Training loss: 1911.7239
Epoch: 1/1 -  Training loss: 1753.7788
Epoch: 1/1 -  Training loss: 1860.8796
Epoch: 1/1 -  Training loss: 2084.8813
Epoch: 1/1 -  Training loss: 1980.8424
Epoch: 1/1 -  Training loss: 2235.1077
Epoch: 1/1 -  Training loss: 1937.0793
Epoch: 1/1 -  Training loss: 2051.2510
Epoch: 1/1 -  Training loss: 2030.3292
Epoch: 1/1 -  Training loss: 1814.5443
Epoch: 1/1 -  Training loss: 1880.8918
Epoch: 1/1 -  Training loss: 1889.2114
Epoch: 1/1 -  Training loss: 1864.2408
Epoch: 1/1 -  Training loss: 1822.2311
Epoch: 1/1 -  Training loss: 1788.6968
Epoch: 1/1 -  Training loss: 1919.6906
Epoch: 1/1 -  Training loss: 1835.6118
Epoch: 1/1 -  Training loss: 1925.8743
Epoch: 1/1 -  Training loss: 1985.6102
Epoch: 1/1 -  Training loss: 1908.7273
Epoch: 1/1 -  Training lo

Epoch: 1/1 -  Training loss: 10544.9814
Epoch: 1/1 -  Training loss: 9738.3828
Epoch: 1/1 -  Training loss: 9383.9766
Epoch: 1/1 -  Training loss: 9638.4131
Epoch: 1/1 -  Training loss: 9893.7686
Epoch: 1/1 -  Training loss: 9951.5137
Epoch: 1/1 -  Training loss: 9978.4541
Epoch: 1/1 -  Training loss: 9993.7041
Epoch: 1/1 -  Training loss: 9843.9531
Epoch: 1/1 -  Training loss: 9430.9688
Epoch: 1/1 -  Training loss: 11297.1006
Epoch: 1/1 -  Training loss: 11201.3213
Epoch: 1/1 -  Training loss: 11027.3145
Epoch: 1/1 -  Training loss: 10915.3945
Epoch: 1/1 -  Training loss: 10459.2080
Epoch: 1/1 -  Training loss: 9948.0459
Epoch: 1/1 -  Training loss: 10326.3242
Epoch: 1/1 -  Training loss: 10353.9922
Epoch: 1/1 -  Training loss: 10327.4502
Epoch: 1/1 -  Training loss: 9599.1816
Epoch: 1/1 -  Training loss: 10123.2969
Epoch: 1/1 -  Training loss: 10208.0312
Epoch: 1/1 -  Training loss: 9511.1670
Epoch: 1/1 -  Training loss: 11408.3691
Epoch: 1/1 -  Training loss: 10055.5283
Epoch: 1/1 -

Epoch: 1/1 -  Training loss: 15.0409
Epoch: 1/1 -  Training loss: 15.2247
Epoch: 1/1 -  Training loss: 14.5052
Epoch: 1/1 -  Training loss: 14.8405
Epoch: 1/1 -  Training loss: 15.0128
Epoch: 1/1 -  Training loss: 13.5760
Epoch: 1/1 -  Training loss: 16.6891
Epoch: 1/1 -  Training loss: 13.6065
Epoch: 1/1 -  Training loss: 13.1096
Epoch: 1/1 -  Training loss: 14.0018
Epoch: 1/1 -  Training loss: 14.1430
Epoch: 1/1 -  Training loss: 13.5399
Epoch: 1/1 -  Training loss: 13.5514
Epoch: 1/1 -  Training loss: 13.1855
Epoch: 1/1 -  Training loss: 12.7483
Epoch: 1/1 -  Training loss: 12.6960
Epoch: 1/1 -  Training loss: 12.6280
Epoch: 1/1 -  Training loss: 11.9657
Epoch: 1/1 -  Training loss: 12.3429
Epoch: 1/1 -  Training loss: 12.4982
Epoch: 1/1 -  Training loss: 12.4746
Epoch: 1/1 -  Training loss: 11.9329
Epoch: 1/1 -  Training loss: 11.9043
Epoch: 1/1 -  Training loss: 12.0909
Epoch: 1/1 -  Training loss: 11.9252
Epoch: 1/1 -  Training loss: 11.8106
Epoch: 1/1 -  Training loss: 12.0250
E

...

Epoch: 1/1 -  Training loss: 0.1982
Epoch: 1/1 -  Training loss: 0.1900
Epoch: 1/1 -  Training loss: 0.1925
Epoch: 1/1 -  Training loss: 0.1866
Epoch: 1/1 -  Training loss: 0.1718
Epoch: 1/1 -  Training loss: 0.1928
Epoch: 1/1 -  Training loss: 0.1793
Epoch: 1/1 -  Training loss: 0.2200
Epoch: 1/1 -  Training loss: 0.2131
Epoch: 1/1 -  Training loss: 0.1873
Epoch: 1/1 -  Training loss: 0.1872
Epoch: 1/1 -  Training loss: 0.6998
Epoch: 1/1 -  Training loss: 0.6944
Epoch: 1/1 -  Training loss: 0.6904
Epoch: 1/1 -  Training loss: 0.6869
Epoch: 1/1 -  Training loss: 0.6840
Epoch: 1/1 -  Training loss: 0.6814
Epoch: 1/1 -  Training loss: 0.6763
Epoch: 1/1 -  Training loss: 0.6736
Epoch: 1/1 -  Training loss: 0.6700
Epoch: 1/1 -  Training loss: 0.6657
Epoch: 1/1 -  Training loss: 0.6610
Epoch: 1/1 -  Training loss: 0.6567
Epoch: 1/1 -  Training loss: 0.6507
Epoch: 1/1 -  Training loss: 0.6476
Epoch: 1/1 -  Training loss: 0.6406
Epoch: 1/1 -  Training loss: 0.6348
Epoch: 1/1 -  Training loss:

Epoch: 1/1 -  Training loss: 0.2331
Epoch: 1/1 -  Training loss: 0.2267
Epoch: 1/1 -  Training loss: 0.2291
Epoch: 1/1 -  Training loss: 0.2317
Epoch: 1/1 -  Training loss: 0.2366
Epoch: 1/1 -  Training loss: 0.2300
Epoch: 1/1 -  Training loss: 0.2306
Epoch: 1/1 -  Training loss: 0.2292
Epoch: 1/1 -  Training loss: 0.2256
Epoch: 1/1 -  Training loss: 0.2302
Epoch: 1/1 -  Training loss: 0.2302
Epoch: 1/1 -  Training loss: 0.2346
Epoch: 1/1 -  Training loss: 0.2321
Epoch: 1/1 -  Training loss: 0.2228
Epoch: 1/1 -  Training loss: 0.2232
Epoch: 1/1 -  Training loss: 0.2375
Epoch: 1/1 -  Training loss: 0.2505
Epoch: 1/1 -  Training loss: 0.2254
Epoch: 1/1 -  Training loss: 0.2369
Epoch: 1/1 -  Training loss: 0.2385
Epoch: 1/1 -  Training loss: 0.2380
Epoch: 1/1 -  Training loss: 0.2310
Epoch: 1/1 -  Training loss: 0.2210
Epoch: 1/1 -  Training loss: 0.2374
Epoch: 1/1 -  Training loss: 0.2301
Epoch: 1/1 -  Training loss: 0.2367
Epoch: 1/1 -  Training loss: 0.2258
Epoch: 1/1 -  Training loss:

Epoch: 1/1 -  Training loss: 0.2606
Epoch: 1/1 -  Training loss: 0.2674
Epoch: 1/1 -  Training loss: 0.2493
Epoch: 1/1 -  Training loss: 0.2414
Epoch: 1/1 -  Training loss: 0.2649
Epoch: 1/1 -  Training loss: 0.2570
Epoch: 1/1 -  Training loss: 0.2455
Epoch: 1/1 -  Training loss: 0.2367
Epoch: 1/1 -  Training loss: 0.2395
Epoch: 1/1 -  Training loss: 0.2452
Epoch: 1/1 -  Training loss: 0.2418
Epoch: 1/1 -  Training loss: 0.2519
Epoch: 1/1 -  Training loss: 0.2540
Epoch: 1/1 -  Training loss: 0.2455
Epoch: 1/1 -  Training loss: 0.2478
Epoch: 1/1 -  Training loss: 0.2430
Epoch: 1/1 -  Training loss: 0.2575
Epoch: 1/1 -  Training loss: 0.2488
Epoch: 1/1 -  Training loss: 0.2497
Epoch: 1/1 -  Training loss: 0.2580
Epoch: 1/1 -  Training loss: 0.2607
Epoch: 1/1 -  Training loss: 0.2563
Epoch: 1/1 -  Training loss: 0.2609
Epoch: 1/1 -  Training loss: 0.2404
Epoch: 1/1 -  Training loss: 0.2489
Epoch: 1/1 -  Training loss: 0.2479
Epoch: 1/1 -  Training loss: 0.2504
Epoch: 1/1 -  Training loss:

Epoch: 1/1 -  Training loss: 0.2588
Epoch: 1/1 -  Training loss: 0.2752
Epoch: 1/1 -  Training loss: 0.2542
Epoch: 1/1 -  Training loss: 0.2596
Epoch: 1/1 -  Training loss: 0.2683
Epoch: 1/1 -  Training loss: 0.2682
Epoch: 1/1 -  Training loss: 0.2700
Epoch: 1/1 -  Training loss: 0.2565
Epoch: 1/1 -  Training loss: 0.2509
Epoch: 1/1 -  Training loss: 0.2565
Epoch: 1/1 -  Training loss: 0.2567
Epoch: 1/1 -  Training loss: 0.2344
Epoch: 1/1 -  Training loss: 0.2502
Epoch: 1/1 -  Training loss: 0.2640
Epoch: 1/1 -  Training loss: 0.2449
Epoch: 1/1 -  Training loss: 0.2325
Epoch: 1/1 -  Training loss: 0.2474
Epoch: 1/1 -  Training loss: 0.2622
Epoch: 1/1 -  Training loss: 0.2475
Epoch: 1/1 -  Training loss: 0.2472
Epoch: 1/1 -  Training loss: 0.2367
Epoch: 1/1 -  Training loss: 0.2411
Epoch: 1/1 -  Training loss: 0.2356
Epoch: 1/1 -  Training loss: 0.2433
Epoch: 1/1 -  Training loss: 0.2445
Epoch: 1/1 -  Training loss: 0.2290
Epoch: 1/1 -  Training loss: 0.2551
Epoch: 1/1 -  Training loss:

Epoch: 1/1 -  Training loss: 0.6692
Epoch: 1/1 -  Training loss: 0.6684
Epoch: 1/1 -  Training loss: 0.6672
Epoch: 1/1 -  Training loss: 0.6674
Epoch: 1/1 -  Training loss: 0.6664
Epoch: 1/1 -  Training loss: 0.6659
Epoch: 1/1 -  Training loss: 0.6656
Epoch: 1/1 -  Training loss: 0.6655
Epoch: 1/1 -  Training loss: 0.6652
Epoch: 1/1 -  Training loss: 0.6648
Epoch: 1/1 -  Training loss: 0.6651
Epoch: 1/1 -  Training loss: 0.6644
Epoch: 1/1 -  Training loss: 0.6638
Epoch: 1/1 -  Training loss: 0.6631
Epoch: 1/1 -  Training loss: 0.6627
Epoch: 1/1 -  Training loss: 0.6624
Epoch: 1/1 -  Training loss: 0.6619
Epoch: 1/1 -  Training loss: 0.6601
Epoch: 1/1 -  Training loss: 0.6584
Epoch: 1/1 -  Training loss: 0.6571
Epoch: 1/1 -  Training loss: 0.6553
Epoch: 1/1 -  Training loss: 0.6533
Epoch: 1/1 -  Training loss: 0.6512
Epoch: 1/1 -  Training loss: 0.6487
Epoch: 1/1 -  Training loss: 0.6458
Epoch: 1/1 -  Training loss: 0.6430
Epoch: 1/1 -  Training loss: 0.6393
Epoch: 1/1 -  Training loss:

## plot batch loss

In [52]:
plot_data = []
for initializer in initializers:
    trace = go.Scatter(
        x = np.arange(len(initializer['loss'])),
        y = initializer['loss'],
        name = initializer['name']
    )
    plot_data.append(trace)

layout = go.Layout(
    title = "Step loss with different weight initialization",
    xaxis=dict(
        showgrid=True,
        title="steps",
    ),
    yaxis=dict(
        showgrid=True,
        title="loss",
        range=[0,1]
    ),
    autosize=True,
    showlegend=True,
)

fig = go.Figure(data=plot_data, layout=layout)
iplot(fig  )

In [51]:
for initializer in initializers:
    print (initializer['name'])


zeros
ones
constant
random_normal
random_uniform
truncated_normal
glorot_normal
glorot_uniform
variance_normal
variance_uniform
orthogonal
identity
